In [1]:
import torch
torch.set_float32_matmul_precision('high')  # Enables Tensor Core optimization


In [1]:
from datetime import date, timedelta
from itertools import combinations
import pandas as pd
import warnings

# Suppress runtime warnings
warnings.filterwarnings("ignore", category=RuntimeWarning)

# ✅ Assuming these modules exist in your local environment
from strategies.macd import MACDStrategy
from strategies.bollinger import BollingerBandsStrategy
from strategies.cci import CCI_Strategy
from strategies.adx import ADXStrategy
from strategies.obv import OBVStrategy

from utils import (
    combine_signals,
    parameter_cache,
    optimize_macd,
    optimize_bollinger_bands,
    optimize_cci,
    optimize_adx
)

from data_loader import fetch_data
from strategy_processor import StrategyProcessor
from backtesting_wrapper_model import BacktestingWrapper

# Configuration
ticker = "AAPL"
start_date = "2024-04-01"
end_date = "2025-04-01"
interval = "1h"
selected_strategies = ["MACD", "BB", "CCI", "ADX", "OBV"]

# Fetch data
data = fetch_data(ticker, start_date, end_date, interval)

# Step 1: Apply strategies and store objects
strategy_objects = {}  # Store for later backtesting
all_processed_data = data.copy()

for strategy_name in selected_strategies:
    if strategy_name == "MACD":
        params = optimize_macd(data, 5, 30)
        strategy = MACDStrategy(
            fast_length=params["fast_length"],
            slow_length=params["slow_length"]
        )
    elif strategy_name == "BB":
        params = optimize_bollinger_bands(data, 5, 25, 1, 3)
        strategy = BollingerBandsStrategy(
            length=params["length"],
            std_dev_multiplier=params["std_dev_multiplier"]
        )
    elif strategy_name == "CCI":
        params = optimize_cci(data, 5, 25)
        strategy = CCI_Strategy(length=params["length"])
    elif strategy_name == "ADX":
        params = optimize_adx(data, 5, 25, 20, 40)
        strategy = ADXStrategy(length=params["length"], threshold=params["threshold"])
    elif strategy_name == "OBV":
        strategy = OBVStrategy()

    # Save the optimized strategy
    strategy_objects[strategy_name] = strategy

    # Process data with strategy
    processor = StrategyProcessor(strategy, data)
    result = processor.process_data()
    all_processed_data[f'BuySignal{strategy_name}'] = result['BuySignal']
    all_processed_data[f'SellSignal{strategy_name}'] = result['SellSignal']

# Step 2: Combine all strategy signals
all_processed_data = combine_signals(all_processed_data, selected_strategies)

# Step 3: Run backtesting
results = []
for r in range(1, len(selected_strategies) + 1):
    for combo in combinations(selected_strategies, r):
        # 🚫 Skip if OBV is used alone
        if combo == ("OBV",):
            continue

        df = all_processed_data.copy()
        if len(combo) == 1:
            s = combo[0]
            df["CommonBuySignal"] = df[f"BuySignal{s}"]
            df["CommonSellSignal"] = df[f"SellSignal{s}"]
        else:
            df = combine_signals(df, list(combo))

        bt = BacktestingWrapper(strategy=None)
        stats = bt.backtest(df, ticker=ticker, interval=interval)
        metrics = bt.extract_statistics(stats)
        results.append({
            "Strategies": " + ".join(combo),
            "Return [%]": metrics['Return [%]'],
            "Trades": metrics['Number of Trades'],
            "Best Trade [$]": metrics['Best Trade [$]'],
            "Worst Trade [$]": metrics['Worst Trade [$]']
        })

# Step 4: Show results
df_results = pd.DataFrame(results)
df_results.sort_values("Return [%]", ascending=False, inplace=True)

df_results


C:\Users\rayyo\anaconda3\Lib\site-packages\backtesting\_plotting.py:50: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support (e.g. PyCharm, Spyder IDE). Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

📥 Fetching 1h data for AAPL from 2024-04-01 to 2025-04-01...


[*********************100%***********************]  1 of 1 completed



[MACD] Top 5 Parameter Combinations:
Fast Length  Slow Length  Return [%]
20           22           9.22      
18           23           6.88      
14           29           4.94      
16           26           3.62      
13           24           1.38      

[BollingerBands] Top 5 Parameter Combinations:
Length     Std Dev Multiplier   Return [%]
13         2.6                  52.62     
13         2.5                  41.48     
13         2.7                  40.02     
9          2.2                  39.12     
11         2.5                  37.98     

[CCI] Top 5 Parameter Combinations:
Length     Return [%]
10         24.44     
11         22.10     
12         18.58     
9          16.56     
8          15.94     

[ADX] Top 5 Parameter Combinations:
Length     Threshold    Return [%]
25         40           -0.81     
24         38           -9.65     
22         38           -10.97    
25         39           -11.11    
24         39           -11.83    
🔺 Buy signal detec

...

Validation: |                                                                                    | 0/? [00:00<…

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Predicting: |                                                                                    | 0/? [00:00<…


📈 Predicted next close price for AAPL: $238.89
📈 Current Price: 243.16, Forecasted Price: 238.89
❌ No BUY executed: Forecast is not higher than current price.


Strategies  Return [%]  Trades  Best Trade [$]  \
11                    CCI + ADX   34.647152       2     2074.519564   
23              CCI + ADX + OBV   34.647152       2     2074.519564   
1                            BB   31.869624       5     1848.797846   
8                      BB + CCI   31.869624       5     1848.797846   
0                          MACD   26.362499      18      616.615669   
3                           ADX   26.309211      12      873.953685   
13                    ADX + OBV   26.309211      12      873.953685   
12                    CCI + OBV   24.655772      14      773.305971   
2                           CCI   17.594680      27      813.608379   
7                    MACD + OBV   15.034604      12      821.462634   
19             MACD + ADX + OBV   12.251998       3     1192.758693   
6                    MACD + ADX   12.251998       3     1192.758693   
20               BB + CCI + ADX    0.000000       0             NaN   
26        MACD + BB + ADX + OBV    0.000000       0             NaN   
24        MACD + BB + CCI + ADX    0.000000       0             NaN   
27       MACD + CCI + ADX + OBV    0.000000       0             NaN   
28         BB + CCI + ADX + OBV    0.000000       0             NaN   
22               BB + ADX + OBV    0.000000       0             NaN   
21               BB + CCI + OBV    0.000000       0             NaN   
25        MACD + BB + CCI + OBV    0.000000       0             NaN   
15              MACD + BB + ADX    0.000000       0             NaN   
18             MACD + CCI + OBV    0.000000       0             NaN   
17             MACD + CCI + ADX    0.000000       0             NaN   
16              MACD + BB + OBV    0.000000       0             NaN   
14              MACD + BB + CCI    0.000000       0             NaN   
10                     BB + OBV    0.000000       0             NaN   
9                      BB + ADX    0.000000       0             NaN   
5                    MACD + CCI    0.000000       0             NaN   
4                     MACD + BB    0.000000       0             NaN   
29  MACD + BB + CCI + ADX + OBV    0.000000       0             NaN   

    Worst Trade [$]  
11      1171.555589  
23      1171.555589  
1          2.562599  
8          2.562599  
0       -291.464223  
3       -233.122607  
13      -233.122607  
12      -268.899001  
2       -635.866207  
7       -786.284769  
19      -163.383750  
6       -163.383750  
20              NaN  
26              NaN  
24              NaN  
27              NaN  
28              NaN  
22              NaN  
21              NaN  
25              NaN  
15              NaN  
18              NaN  
17              NaN  
16              NaN  
14              NaN  
10              NaN  
9               NaN  
5               NaN  
4               NaN  
29              NaN